# CISC-873-DM-W23-A2
# Whether a first date will lead to a relationship

https://www.kaggle.com/competitions/cisc-873-dm-w23-a2

# Problem Formulation:
Define the problem. What is the input? What is the output? What data mining function is required? What could be the challenges? What is the impact? What is an ideal solution?

**Define the problem**

We need to predict the outcome of a specific speed dating session based on the profile of two people, so we can implement a recommendation system to better match people in speed dating events. but the given data has a lot of missing values that must be handled to perform the model well.

**What is the input?**

we have some features for each participant ,this will help us to know some information about Participants,and predict exactly

**What is the output?** 

The output is which the two people matches or not matched based on the features.

**What data mining function is required?**

a binary classification function

**What could be the challenges?**
* The data have alot of missing value should be handled
* we should select best classifier for classify more accurate
* use feature selection to know what is the important features can give us high predict
  
**What is the impact?**

The recommendation system can select two person that perfectly match each other based on their answers in the application
   
**What is an ideal solution?**

handleing of  missing data perfectly and select the best hyperparameters that gives high performance
in case of my trials i notice that the Xgbclassifier did this perfectly


### Answer the questions below (briefly):

1-***Why a simple linear regression model (without any activation function) is not good for classification task, compared to Perceptron/Logistic regression?***

There are two things that explain why Linear Regression is not suitable for classification.

`The first` one is that Linear Regression deals with continuous values whereas classification problems mandate discrete values.

`The second` problem is regarding the shift in threshold value when new data points are added. 

* Logistic regression provides discreet output

* the perceptron can be used as a binary classification model, defining a linear decision boundary. It finds the separating hyperplane that minimizes the distance between misclassified points and the decision boundary

***************

2- ***What's a decision tree and how it is different to a logistic regression model?***

`Decision Tree`: is a Supervised learning technique that can be used for both classification and Regression problems, but mostly it is preferred for solving Classification problems. It is a tree-structured classifier

**Different to a logistic regression model**

1-Logistic Regression assumes that the data is linearly (or curvy linearly)
Decision Trees are non-linear classifiers

2-Categorical data works well with Decision Trees, while continuous data work well with Logistic Regression

3-Logistic Regression does not handle skewed classes well,Decision Trees handle skewed classes nicely if we let it grow fully.

4-Decision Trees works with missing values,
Logistic Regression does not handle missing values


***************

3- ***What's the difference between grid search and random search?***

* Random search differs from grid search in that we no longer provide an explicit set of possible values for each hyperparameter; rather, we provide a statistical distribution for each hyperparameter from which values are sampled. Essentially, we define a sampling distribution for each hyperparameter to carry out a randomized search

* Grid search is not very often used in practice because the number of models to train grows exponentially as you increase the number of hyperparameters to train. This can be very inefficient — both in computing power and time.

*****************

4-***What's the difference between bayesian search and random search?***
`Random search`

* Try out a random subset 

* good enough

* Local optimal (within the given range)

* Efficient (less trials)

* Sklearn: model_selection.RandomizedSearchCV

`Bayesian Optimization`

* As an optimization problem

* Trial -> estimated error -> Bayesian model estimates the next 

* parameter to try -> trial -> repeat

* pip install bayesian-optimization


### Import libraries

In [79]:
import numpy as np #used for working with arrays
import pandas as pd #Pandas is mainly used for data analysis
pd.set_option("display.max_rows", None, "display.max_columns", None)
import matplotlib.pyplot as plt #is a cross-platform, data visualization and graphical plotting library
from sklearn.compose import make_column_selector as selector
from sklearn.compose import ColumnTransformer

from sklearn.datasets import fetch_openml
from sklearn.pipeline import Pipeline #pipeline is a way to codify and automate the workflow
from sklearn.impute import SimpleImputer #Imputation transformer for completing missing values.

from sklearn.feature_selection import SelectKBest, mutual_info_classif
# SelectKBest: Select features according to the k highest scores.
# mutual_info_classif: Estimate mutual information for a discrete target variable.
# In short, it is the amount of information one variable gives about the other.

from sklearn.preprocessing import StandardScaler, OneHotEncoder #Standardize features by removing the mean and scaling to unit variance.
# one hot encoding is essential process of converting the categorical to numeric
from sklearn.model_selection import train_test_split, GridSearchCV#Tuning the hyper-parameters
from skopt import BayesSearchCV #use bayessearchcv for tuning hyperparameter with cross validation k=5

from xgboost.sklearn import XGBClassifier
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.tree import DecisionTreeClassifier
import warnings #handling warning 
warnings.filterwarnings('ignore')

 make_column_selector:
- Create a callable to select columns to be used with ColumnTransformer.

 ColumnTransformer: 
- Applies transformers to columns of an array or pandas DataFrame. This estimator allows different columns or column subsets of the input to be transformed separately and the features generated by each transformer will be concatenatedto form a single feature space

fetch_openml
- Fetch dataset from openml by name or dataset id.

### Train and Test sets

In [2]:
df1 = pd.read_csv('train.csv')# read train file 
print(df1.shape)#shape of train data
df1.head(2)

(5909, 192)


gender  idg  condtn  wave  round  position  positin1  order  partner  \
0       0    3       2    14     18         2       2.0     14       12   
1       1   14       1     3     10         2       NaN      8        8   

     pid  match  int_corr  samerace  age_o  race_o  pf_o_att  pf_o_sin  \
0  372.0      0     -0.03         0   27.0     2.0      30.0      15.0   
1   63.0      0      0.21         0   24.0     4.0       5.0      15.0   

   pf_o_int  pf_o_fun  pf_o_amb  pf_o_sha  attr_o  sinc_o  intel_o  fun_o  \
0      15.0      20.0       5.0      15.0     7.0     7.0      7.0    6.0   
1      45.0      25.0       0.0      10.0     3.0     8.0      5.0    3.0   

   amb_o  shar_o  like_o  prob_o  met_o   age  \
0    5.0     NaN     7.0     1.0    2.0  33.0   
1    7.0     1.0     1.0     3.0    2.0  22.0   

                                    field  field_cd  \
0  Ed.D. in higher education policy at TC       9.0   
1                             Engineering       5.0   

                           undergra    mn_sat    tuition  race  imprace  \
0  University of Michigan-Ann Arbor  1,290.00  21,645.00   3.0      2.0   
1                               NaN       NaN        NaN   2.0      8.0   

   imprelig           from zipcode income  goal  date  go_out  \
0       1.0  Palo Alto, CA     NaN    NaN   1.0   6.0     3.0   
1       1.0     Boston, MA   2,021    NaN   5.0   6.0     1.0   

                              career  career_c  sports  tvsports  exercise  \
0               University President       2.0     3.0       4.0       4.0   
1  Engineer or iBanker or consultant       7.0     8.0       3.0       7.0   

   dining  museums   art  hiking  gaming  clubbing  reading    tv  theater  \
0    10.0      9.0  10.0     1.0     1.0       8.0      7.0  10.0      8.0   
1    10.0      6.0   6.0     7.0     2.0       9.0      5.0   6.0      7.0   

   movies  concerts  music  shopping  yoga  exphappy  expnum  attr1_1  \
0    10.0       1.0    4.0      10.0   4.0       2.0     NaN     40.0   
1     7.0       6.0    8.0       8.0   4.0       7.0     9.0     21.0   

   sinc1_1  intel1_1  fun1_1  amb1_1  shar1_1  attr4_1  sinc4_1  intel4_1  \
0     15.0      25.0     5.0    15.0      0.0     55.0     10.0       5.0   
1     20.0      19.0    20.0    10.0     10.0      NaN      NaN       NaN   

   fun4_1  amb4_1  shar4_1  attr2_1  sinc2_1  intel2_1  fun2_1  amb2_1  \
0    15.0     5.0     10.0     70.0      5.0       5.0    15.0     5.0   
1     NaN     NaN      NaN     30.0     15.0      10.0    20.0    10.0   

   shar2_1  attr3_1  sinc3_1  fun3_1  intel3_1  amb3_1  attr5_1  sinc5_1  \
0      0.0     10.0     10.0    10.0      10.0    10.0     10.0     10.0   
1     15.0      7.0      9.0     8.0       8.0     8.0      NaN      NaN   

   intel5_1  fun5_1  amb5_1  attr  sinc  intel  fun  amb  shar  like  prob  \
0      10.0    10.0    10.0   6.0   5.0    7.0  6.0  6.0   NaN   6.0   4.0   
1       NaN     NaN     NaN   5.0   8.0    8.0  5.0  7.0   6.0   6.0   6.0   

   met  match_es  attr1_s  sinc1_s  intel1_s  fun1_s  amb1_s  shar1_s  \
0  0.0       6.0      NaN      NaN       NaN     NaN     NaN      NaN   
1  2.0       1.0      NaN      NaN       NaN     NaN     NaN      NaN   

   attr3_s  sinc3_s  intel3_s  fun3_s  amb3_s  satis_2  length  numdat_2  \
0      NaN      NaN       NaN     NaN     NaN      9.0     1.0       2.0   
1      NaN      NaN       NaN     NaN     NaN      6.0     1.0       3.0   

   attr7_2  sinc7_2  intel7_2  fun7_2  amb7_2  shar7_2  attr1_2  sinc1_2  \
0      NaN      NaN       NaN     NaN     NaN      NaN     60.0     10.0   
1      NaN      NaN       NaN     NaN     NaN      NaN     22.0     17.0   

   intel1_2  fun1_2  amb1_2  shar1_2  attr4_2  sinc4_2  intel4_2  fun4_2  \
0      10.0    10.0    10.0      0.0     45.0     25.0       5.0    25.0   
1      17.0    17.0    10.0     17.0      NaN      NaN       NaN     NaN   

   amb4_2  shar4_2  attr2_2  sinc2_2  intel2_2  fun2_2  amb2_2  shar2_

In [3]:
df2 = pd.read_csv('test.csv')#read test file 
print(df2.shape)#shape of test data 
df2.head(2)

(2469, 191)


gender  idg  condtn  wave  round  position  positin1  order  partner  \
0       0    5       2     2     16         3       NaN     13       13   
1       0   33       2    14     18         6       6.0      4        8   

     pid  int_corr  samerace  age_o  race_o  pf_o_att  pf_o_sin  pf_o_int  \
0   52.0     -0.13         0   21.0     2.0      15.0      20.0      15.0   
1  368.0      0.12         0   24.0     6.0      20.0      10.0      25.0   

   pf_o_fun  pf_o_amb  pf_o_sha  attr_o  sinc_o  intel_o  fun_o  amb_o  \
0      30.0       5.0      15.0     7.0     7.0      6.0    6.0    6.0   
1      20.0      10.0      15.0     7.0     9.0      8.0    8.0    7.0   

   shar_o  like_o  prob_o  met_o   age       field  field_cd  \
0     5.0     5.0     2.0    2.0  21.0  Psychology       3.0   
1     7.0     6.0     7.0    2.0  27.0   education       9.0   

            undergra    mn_sat    tuition  race  imprace  imprelig  \
0                NaN       NaN        NaN   4.0      9.0       6.0   
1  wellesley college  1,341.00  25,504.00   4.0     10.0      10.0   

          from zipcode     income  goal  date  go_out        career  career_c  \
0    Hong Kong       0        NaN   1.0   1.0     1.0  psychologist       3.0   
1  atlanta, ga  30,071  36,223.00   1.0   4.0     2.0     education       2.0   

   sports  tvsports  exercise  dining  museums   art  hiking  gaming  \
0     2.0       2.0       3.0     9.0      7.0   6.0     6.0     7.0   
1     2.0       6.0      10.0    10.0     10.0  10.0     8.0     1.0   

   clubbing  reading   tv  theater  movies  concerts  music  shopping  yoga  \
0       7.0     10.0  9.0     10.0    10.0      10.0   10.0      10.0   3.0   
1       7.0     10.0  6.0     10.0     8.0       7.0    7.0       8.0   1.0   

   exphappy  expnum  attr1_1  sinc1_1  intel1_1  fun1_1  amb1_1  shar1_1  \
0       5.0     3.0     10.0     20.0      40.0    10.0    10.0     10.0   
1       1.0     NaN     15.0     20.0      20.0    20.0    20.0      5.0   

   attr4_1  sinc4_1  intel4_1  fun4_1  amb4_1  shar4_1  attr2_1  sinc2_1  \
0      NaN      NaN       NaN     NaN     NaN      NaN     40.0      5.0   
1     15.0     20.0      15.0    20.0    10.0     20.0     60.0      0.0   

   intel2_1  fun2_1  amb2_1  shar2_1  attr3_1  sinc3_1  fun3_1  intel3_1  \
0      20.0    20.0     5.0     10.0      5.0      8.0     6.0       7.0   
1       5.0    20.0     0.0     15.0      6.0     10.0     7.0       7.0   

   amb3_1  attr5_1  sinc5_1  intel5_1  fun5_1  amb5_1  attr  sinc  intel  fun  \
0     8.0      NaN      NaN       NaN     NaN     NaN   6.0   6.0    5.0  7.0   
1     6.0      7.0      7.0       6.0     6.0     6.0   4.0   8.0    8.0  9.0   

   amb  shar  like  prob  met  match_es  attr1_s  sinc1_s  intel1_s  fun1_s  \
0  5.0   6.0   6.0   5.0  2.0       3.0      NaN      NaN       NaN     NaN   
1  NaN   8.0   7.0   6.0  0.0       1.0      NaN      NaN       NaN     NaN   

   amb1_s  shar1_s  attr3_s  sinc3_s  intel3_s  fun3_s  amb3_s  satis_2  \
0     NaN      NaN      NaN      NaN       NaN     NaN     NaN      7.0   
1     NaN      NaN      NaN      NaN       NaN     NaN     NaN      3.0   

   length  numdat_2  attr7_2  sinc7_2  intel7_2  fun7_2  amb7_2  shar7_2  \
0     2.0       2.0      NaN      NaN       NaN     NaN     NaN      NaN   
1     3.0       2.0      NaN      NaN       NaN     NaN     NaN      NaN   

   attr1_2  sinc1_2  intel1_2  fun1_2  amb1_2  shar1_2  attr4_2  sinc4_2  \
0     10.0     10.0      30.0    20.0    10.0     20.0      NaN      NaN   
1     20.0     10.0      30.0    20.0    15.0     15.0     25.0     15.0   

   intel4_2  fun4_2  amb4_2  shar4_2  attr2_2  sinc2_2  intel2_2  fun2_2  \
0       NaN     NaN     NaN      NaN      NaN      NaN       NaN     NaN   
1      15.0    20.0     5.0     20.0     30.0     10.0      10.0    30.0   

   amb2_2  shar2_2  attr3_2  sinc3_2  intel3_2  fun3_2  amb3_2  attr5_2  \
0     NaN      NaN      5.0      7.0       7.0     6.0     7.0

In [4]:
df2['match'] = 0 #add column match to test file before concat

### Concatinating the Data

In [5]:
#I concat train and test data to deal with all data and then I will split it
all_data= pd.concat([df1,df2],ignore_index=True, sort=False)
all_data.head(2)

gender  idg  condtn  wave  round  position  positin1  order  partner  \
0       0    3       2    14     18         2       2.0     14       12   
1       1   14       1     3     10         2       NaN      8        8   

     pid  match  int_corr  samerace  age_o  race_o  pf_o_att  pf_o_sin  \
0  372.0      0     -0.03         0   27.0     2.0      30.0      15.0   
1   63.0      0      0.21         0   24.0     4.0       5.0      15.0   

   pf_o_int  pf_o_fun  pf_o_amb  pf_o_sha  attr_o  sinc_o  intel_o  fun_o  \
0      15.0      20.0       5.0      15.0     7.0     7.0      7.0    6.0   
1      45.0      25.0       0.0      10.0     3.0     8.0      5.0    3.0   

   amb_o  shar_o  like_o  prob_o  met_o   age  \
0    5.0     NaN     7.0     1.0    2.0  33.0   
1    7.0     1.0     1.0     3.0    2.0  22.0   

                                    field  field_cd  \
0  Ed.D. in higher education policy at TC       9.0   
1                             Engineering       5.0   

                           undergra    mn_sat    tuition  race  imprace  \
0  University of Michigan-Ann Arbor  1,290.00  21,645.00   3.0      2.0   
1                               NaN       NaN        NaN   2.0      8.0   

   imprelig           from zipcode income  goal  date  go_out  \
0       1.0  Palo Alto, CA     NaN    NaN   1.0   6.0     3.0   
1       1.0     Boston, MA   2,021    NaN   5.0   6.0     1.0   

                              career  career_c  sports  tvsports  exercise  \
0               University President       2.0     3.0       4.0       4.0   
1  Engineer or iBanker or consultant       7.0     8.0       3.0       7.0   

   dining  museums   art  hiking  gaming  clubbing  reading    tv  theater  \
0    10.0      9.0  10.0     1.0     1.0       8.0      7.0  10.0      8.0   
1    10.0      6.0   6.0     7.0     2.0       9.0      5.0   6.0      7.0   

   movies  concerts  music  shopping  yoga  exphappy  expnum  attr1_1  \
0    10.0       1.0    4.0      10.0   4.0       2.0     NaN     40.0   
1     7.0       6.0    8.0       8.0   4.0       7.0     9.0     21.0   

   sinc1_1  intel1_1  fun1_1  amb1_1  shar1_1  attr4_1  sinc4_1  intel4_1  \
0     15.0      25.0     5.0    15.0      0.0     55.0     10.0       5.0   
1     20.0      19.0    20.0    10.0     10.0      NaN      NaN       NaN   

   fun4_1  amb4_1  shar4_1  attr2_1  sinc2_1  intel2_1  fun2_1  amb2_1  \
0    15.0     5.0     10.0     70.0      5.0       5.0    15.0     5.0   
1     NaN     NaN      NaN     30.0     15.0      10.0    20.0    10.0   

   shar2_1  attr3_1  sinc3_1  fun3_1  intel3_1  amb3_1  attr5_1  sinc5_1  \
0      0.0     10.0     10.0    10.0      10.0    10.0     10.0     10.0   
1     15.0      7.0      9.0     8.0       8.0     8.0      NaN      NaN   

   intel5_1  fun5_1  amb5_1  attr  sinc  intel  fun  amb  shar  like  prob  \
0      10.0    10.0    10.0   6.0   5.0    7.0  6.0  6.0   NaN   6.0   4.0   
1       NaN     NaN     NaN   5.0   8.0    8.0  5.0  7.0   6.0   6.0   6.0   

   met  match_es  attr1_s  sinc1_s  intel1_s  fun1_s  amb1_s  shar1_s  \
0  0.0       6.0      NaN      NaN       NaN     NaN     NaN      NaN   
1  2.0       1.0      NaN      NaN       NaN     NaN     NaN      NaN   

   attr3_s  sinc3_s  intel3_s  fun3_s  amb3_s  satis_2  length  numdat_2  \
0      NaN      NaN       NaN     NaN     NaN      9.0     1.0       2.0   
1      NaN      NaN       NaN     NaN     NaN      6.0     1.0       3.0   

   attr7_2  sinc7_2  intel7_2  fun7_2  amb7_2  shar7_2  attr1_2  sinc1_2  \
0      NaN      NaN       NaN     NaN     NaN      NaN     60.0     10.0   
1      NaN      NaN       NaN     NaN     NaN      NaN     22.0     17.0   

   intel1_2  fun1_2  amb1_2  shar1_2  attr4_2  sinc4_2  intel4_2  fun4_2  \
0      10.0    10.0    10.0      0.0     45.0     25.0       5.0    25.0   
1      17.0    17.0    10.0     17.0      NaN      NaN       NaN     NaN   

   amb4_2  shar4_2  attr2_2  sinc2_2  intel2_2  fun2_2  amb2_2  shar2_

In [6]:
all_data.dtypes

gender        int64
idg           int64
condtn        int64
wave          int64
round         int64
position      int64
positin1    float64
order         int64
partner       int64
pid         float64
match         int64
int_corr    float64
samerace      int64
age_o       float64
race_o      float64
pf_o_att    float64
pf_o_sin    float64
pf_o_int    float64
pf_o_fun    float64
pf_o_amb    float64
pf_o_sha    float64
attr_o      float64
sinc_o      float64
intel_o     float64
fun_o       float64
amb_o       float64
shar_o      float64
like_o      float64
prob_o      float64
met_o       float64
age         float64
field        object
field_cd    float64
undergra     object
mn_sat       object
tuition      object
race        float64
imprace     float64
imprelig    float64
from         object
zipcode      object
income       object
goal        float64
date        float64
go_out      float64
career       object
career_c    float64
sports      float64
tvsports    float64
exercise    float64


In [7]:
all_data.nunique()

gender         2
idg           44
condtn         2
wave          21
round         15
position      22
positin1      22
order         22
partner       22
pid          551
match          2
int_corr     155
samerace       2
age_o         24
race_o         5
pf_o_att      94
pf_o_sin      78
pf_o_int      65
pf_o_fun      71
pf_o_amb      82
pf_o_sha      85
attr_o        18
sinc_o        14
intel_o       17
fun_o         17
amb_o         15
shar_o        15
like_o        18
prob_o        19
met_o          7
age           24
field        259
field_cd      18
undergra     241
mn_sat        68
tuition      115
race           5
imprace       11
imprelig      10
from         269
zipcode      409
income       261
goal           6
date           7
go_out         7
career       367
career_c      17
sports        10
tvsports      10
exercise      10
dining        10
museums       11
art           11
hiking        11
gaming        12
clubbing      11
reading       11
tv            10
theater       

### check for missing values

In [8]:
all_data.isnull().sum().sort_values(ascending=False)
# looks like all columns has missing value :D

num_in_3    7710
numdat_3    6882
expnum      6578
amb7_2      6423
sinc7_2     6423
shar7_2     6404
fun7_2      6394
intel7_2    6394
attr7_2     6394
attr7_3     6362
sinc7_3     6362
intel7_3    6362
fun7_3      6362
amb7_3      6362
shar7_3     6362
shar2_3     6362
attr5_3     6362
sinc5_3     6362
intel5_3    6362
fun5_3      6362
amb5_3      6362
shar4_3     5419
fun4_3      5419
intel4_3    5419
sinc4_3     5419
attr4_3     5419
attr2_3     5419
sinc2_3     5419
intel2_3    5419
fun2_3      5419
amb2_3      5419
amb4_3      5419
mn_sat      5245
tuition     4795
attr1_3     4404
intel1_3    4404
amb3_3      4404
sinc3_3     4404
intel3_3    4404
shar1_3     4404
amb1_3      4404
fun1_3      4404
fun3_3      4404
attr3_3     4404
sinc1_3     4404
date_3      4404
you_call    4404
them_cal    4404
amb3_s      4378
sinc3_s     4378
intel3_s    4378
fun3_s      4378
attr3_s     4378
shar1_s     4282
amb1_s      4282
fun1_s      4282
intel1_s    4282
sinc1_s     4282
attr1_s     42

In [9]:
#this return the first 50 columns have null value 
null_val = pd.DataFrame(all_data.isnull().sum())
null_val.columns = ['null_val']
null_val['percent_'] = round(null_val['null_val'] / len(all_data.index), 2) * 100
nulls = null_val.sort_values('percent_', ascending = False)[:50]  # percent of null value for each columns

In [10]:
nulls

null_val  percent_
num_in_3      7710      92.0
numdat_3      6882      82.0
expnum        6578      79.0
amb7_2        6423      77.0
sinc7_2       6423      77.0
shar2_3       6362      76.0
fun7_3        6362      76.0
intel7_3      6362      76.0
sinc7_3       6362      76.0
attr7_3       6362      76.0
shar7_2       6404      76.0
intel7_2      6394      76.0
fun7_2        6394      76.0
shar7_3       6362      76.0
attr7_2       6394      76.0
attr5_3       6362      76.0
sinc5_3       6362      76.0
intel5_3      6362      76.0
fun5_3        6362      76.0
amb5_3        6362      76.0
amb7_3        6362      76.0
amb2_3        5419      65.0
attr4_3       5419      65.0
shar4_3       5419      65.0
intel4_3      5419      65.0
fun4_3        5419      65.0
amb4_3        5419      65.0
fun2_3        5419      65.0
intel2_3      5419      65.0
sinc2_3       5419      65.0
sinc4_3       5419      65.0
attr2_3       5419      65.0
mn_sat        5245      63.0
tuition       4795      57.0
attr1_3       4404      53.0
intel1_3      4404      53.0
shar1_3       4404      53.0
attr3_3       4404      53.0
fun3_3        4404      53.0
intel3_3      4404      53.0
amb1_3        4404      53.0
sinc3_3       4404      53.0
fun1_3        4404      53.0
amb3_3        4404      53.0
sinc1_3       4404      53.0
date_3        4404      53.0
you_call      4404      53.0
them_cal      4404      53.0
attr3_s       4378      52.0
amb3_s        4378      52.0

In [11]:
nulls.index.values

array(['num_in_3', 'numdat_3', 'expnum', 'amb7_2', 'sinc7_2', 'shar2_3',
       'fun7_3', 'intel7_3', 'sinc7_3', 'attr7_3', 'shar7_2', 'intel7_2',
       'fun7_2', 'shar7_3', 'attr7_2', 'attr5_3', 'sinc5_3', 'intel5_3',
       'fun5_3', 'amb5_3', 'amb7_3', 'amb2_3', 'attr4_3', 'shar4_3',
       'intel4_3', 'fun4_3', 'amb4_3', 'fun2_3', 'intel2_3', 'sinc2_3',
       'sinc4_3', 'attr2_3', 'mn_sat', 'tuition', 'attr1_3', 'intel1_3',
       'shar1_3', 'attr3_3', 'fun3_3', 'intel3_3', 'amb1_3', 'sinc3_3',
       'fun1_3', 'amb3_3', 'sinc1_3', 'date_3', 'you_call', 'them_cal',
       'attr3_s', 'amb3_s'], dtype=object)

In [12]:
# Drop featues has above 52% null values (50 feature)
all_data = all_data.drop([
    'num_in_3', 'numdat_3', 'expnum', 'amb7_2', 'sinc7_2', 'shar2_3',
       'fun7_3', 'intel7_3', 'sinc7_3', 'attr7_3', 'shar7_2', 'intel7_2',
       'fun7_2', 'shar7_3', 'attr7_2', 'attr5_3', 'sinc5_3', 'intel5_3',
       'fun5_3', 'amb5_3', 'amb7_3', 'amb2_3', 'attr4_3', 'shar4_3',
       'intel4_3', 'fun4_3', 'amb4_3', 'fun2_3', 'intel2_3', 'sinc2_3',
       'sinc4_3', 'attr2_3', 'mn_sat', 'tuition', 'attr1_3', 'intel1_3',
       'shar1_3', 'attr3_3', 'fun3_3', 'intel3_3', 'amb1_3', 'sinc3_3',
       'fun1_3', 'amb3_3', 'sinc1_3', 'date_3', 'you_call', 'them_cal',
       'attr3_s', 'amb3_s'
],  axis =1)

In [13]:
all_data.isnull().sum().sort_values(ascending=False)

intel3_s    4378
fun3_s      4378
sinc3_s     4378
intel1_s    4282
amb1_s      4282
shar1_s     4282
fun1_s      4282
attr1_s     4282
sinc1_s     4282
income      4099
fun5_2      4001
sinc5_2     4001
attr5_2     4001
amb5_2      4001
intel5_2    4001
amb5_1      3472
fun5_1      3472
sinc5_1     3472
attr5_1     3472
intel5_1    3472
undergra    3464
shar2_2     2603
attr4_2     2603
sinc4_2     2603
intel4_2    2603
fun4_2      2603
amb4_2      2603
shar4_2     2603
attr2_2     2603
sinc2_2     2603
intel2_2    2603
fun2_2      2603
amb2_2      2603
shar4_1     1911
amb4_1      1889
fun4_1      1889
sinc4_1     1889
attr4_1     1889
intel4_1    1889
positin1    1846
match_es    1173
shar_o      1076
shar        1067
zipcode     1064
numdat_2     945
attr1_2      933
intel3_2     915
length       915
amb3_2       915
fun3_2       915
sinc3_2      915
shar1_2      915
satis_2      915
attr3_2      915
sinc1_2      915
intel1_2     915
fun1_2       915
amb1_2       915
amb_o        7

In [14]:
# Make a copy to make some simple transformation to the data
data = all_data.copy()

In [15]:
#data=data.set_index('id')#set id as index
print(data.shape)
data.head()

(8378, 142)


gender  idg  condtn  wave  round  position  positin1  order  partner  \
0       0    3       2    14     18         2       2.0     14       12   
1       1   14       1     3     10         2       NaN      8        8   
2       1   14       1    13     10         8       8.0     10       10   
3       1   38       2     9     20        18      13.0      6        7   
4       1   24       2    14     20         6       6.0     20       17   

     pid  match  int_corr  samerace  age_o  race_o  pf_o_att  pf_o_sin  \
0  372.0      0     -0.03         0   27.0     2.0     30.00     15.00   
1   63.0      0      0.21         0   24.0     4.0      5.00     15.00   
2  331.0      0      0.43         0   34.0     2.0     15.00     15.00   
3  200.0      0      0.72         1   25.0     2.0     13.21     18.87   
4  357.0      0      0.33         0   27.0     4.0     15.00     20.00   

   pf_o_int  pf_o_fun  pf_o_amb  pf_o_sha  attr_o  sinc_o  intel_o  fun_o  \
0     15.00     20.00      5.00     15.00     7.0     7.0      7.0    6.0   
1     45.00     25.00      0.00     10.00     3.0     8.0      5.0    3.0   
2     10.00     25.00     10.00     25.00     4.0     8.0      7.0    4.0   
3     18.87     16.98     16.98     15.09     5.0     9.0      7.0    5.0   
4     20.00     20.00     20.00      5.00     4.0     5.0      7.0    5.0   

   amb_o  shar_o  like_o  prob_o  met_o   age  \
0    5.0     NaN     7.0     1.0    2.0  33.0   
1    7.0     1.0     1.0     3.0    2.0  22.0   
2    7.0     3.0     3.0     2.0    2.0  27.0   
3    8.0     NaN     7.0     6.0    2.0  31.0   
4    5.0     6.0     4.0     3.0    2.0  27.0   

                                    field  field_cd  \
0  Ed.D. in higher education policy at TC       9.0   
1                             Engineering       5.0   
2                          Urban Planning       5.0   
3                   International Affairs      13.0   
4                                Business       8.0   

                                           undergra  race  imprace  imprelig  \
0                  University of Michigan-Ann Arbor   3.0      2.0       1.0   
1                                               NaN   2.0      8.0       1.0   
2  Rizvi College of Architecture, Bombay University   6.0      1.0       1.0   
3                                               NaN   2.0      4.0       7.0   
4                                   Harvard College   2.0      9.0       7.0   

             from zipcode     income  goal  date  go_out  \
0   Palo Alto, CA     NaN        NaN   1.0   6.0     3.0   
1      Boston, MA   2,021        NaN   5.0   6.0     1.0   
2   Bombay, India     NaN        NaN   1.0   4.0     2.0   
3  Washington, DC  10,471  45,300.00   2.0   5.0     4.0   
4     Midwest USA  66,208  46,138.00   2.0   5.0     2.0   

                              career  career_c  sports  tvsports  exercise  \
0               University President       2.0     3.0       4.0       4.0   
1  Engineer or iBanker or consultant       7.0     8.0       3.0       7.0   
2             Real Estate Consulting       7.0     4.0       2.0       7.0   
3                     public service       9.0     5.0       5.0       9.0   
4                          undecided      10.0     9.0      10.0       8.0   

   dining  museums   art  hiking  gaming  clubbing  reading    tv  theater  \
0    10.0      9.0  10.0     1.0     1.0       8.0      7.0  10.0      8.0   
1    10.0      6.0   6.0     7.0     2.0       9.0      5.0   6.0      7.0   
2     6.0      8.0   8.0     8.0     6.0       6.0      8.0   4.0     10.0   
3     8.0      7.0   8.0     9.0     3.0       8.0      7.0   4.0      6.0   
4     9.0      9.0   9.0     7.0     4.0       2.0      9.0   6.0      8.0   

   movies  concerts  music  shopping  yoga  exphappy  attr1_1  sinc1_1  \
0    10.0       1.0    4.0      10.0   4.0       2.0    40.00    15.00   
1     7.0       6.0    8.0       8.0   4.0       7.0    21.00    20.00   
2    10.0       

### Categorical data

In [16]:
#all categorical data on dataset
categorical_columns_selector = selector(dtype_include=object) #select columns that have object as type
categorical_columns = categorical_columns_selector(data)
data_categorical =data[categorical_columns]
print(data_categorical.shape)
data_categorical

(8378, 6)


field  \
0                Ed.D. in higher education policy at TC   
1                                           Engineering   
2                                        Urban Planning   
3                                 International Affairs   
4                                              Business   
5                Ed.D. in higher education policy at TC   
6                                                   MBA   
7                            Operations Research (SEAS)   
8                                                french   
9                                             nutrition   
10                           MA Teaching Social Studies   
11                                            Education   
12                               Electrical Engineering   
13                                  Operations Research   
14                               electrical engineering   
15                                                  MBA   
16                                             Business   
17                                             business   
18                                            sociology   
19                                                  Law   
20                                               french   
21                                              Ecology   
22                                International Affairs   
23                                International Affairs   
24                                             Genetics   
25                                                  MBA   
26                                    School Psychology   
27                                         Human Rights   
28                               Electrical Engineering   
29                           MA in Quantitative Methods   
30                                          Mathematics   
31                                     Climate Dynamics   
32                                             Genetics   
33                                    Finance/Economics   
34                                                  LAW   
35                                              History   
36                  Biochemistry & Molecular Biophysics   
37                                          Social Work   
38                                 MA Science Education   
39                                                  MBA   
40                                                  Law   
41                                                 film   
42                                                  law   
43                                             Business   
44                 International Security Policy - SIPA   
45                                            Sociology   
46                                              Physics   
47                                             medicine   
48                                             business   
49                                              History   
50                            International Development   
51                                       climate change   
52                                             Business   
53                                              Ecology   
54                   Curriculum and Teaching/Giftedness   
55                                       Urban Planning   
56                                             Business   
57                      Master in Public Administration   
58                                         Neurobiology   
59                                                  Law   
60                                             business   
61                                                  MBA   
62                                     Climate Dynamics   
63                                                  MBA   
64                                             Genetics   
65                                              Biology   
66                               Biomedical Engineering   
67                                    

In [17]:
# categorical encoding of columns
data['field'] = data['field'].astype("category")
data['from'] = data['from'].astype("category")
data['undergra'] = data['undergra'].astype("category")
data['zipcode'] = data['zipcode'].astype("category")
data['career'] = data['career'].astype("category")
data['income'] = data['income'].astype("category")

In [18]:
data.shape

(8378, 142)

In [19]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8378 entries, 0 to 8377
Columns: 142 entries, gender to id
dtypes: category(6), float64(125), int64(11)
memory usage: 8.9 MB


In [20]:
#split data into train and test (we concatinated them at first)

train_data_index = df1.shape[0]
train_data = data.iloc[:train_data_index]
train_data_cleaned_index = data.shape[0]
print(train_data.shape)

test_data_index = df2.shape[0]
print(test_data_index)
test_data= data.iloc[train_data_index :]
print(test_data.shape)
test_data= test_data.drop('match', axis=1)  # drop column match from test data (we added it at first)

(5909, 142)
2469
(2469, 142)


In [21]:
train_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5909 entries, 0 to 5908
Columns: 142 entries, gender to id
dtypes: category(6), float64(125), int64(11)
memory usage: 6.3 MB


In [22]:
test_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2469 entries, 5909 to 8377
Columns: 141 entries, gender to id
dtypes: category(6), float64(125), int64(10)
memory usage: 2.6 MB


In [23]:
#split train file to X_train and y_train
X_train=train_data.drop('match',axis=1)

In [24]:
y_train=train_data['match']#label

# Pipeline and models

In [25]:
#extract numeric features and categorical features names

numeric_features = list(X_train.select_dtypes(include=['float64', 'int64']))

categorical_features = list(X_train.select_dtypes(include=['category']))

print('numeric features:', numeric_features)
print('-----------------------------------------------------------')
print('categorical features:', categorical_features)

numeric features: ['gender', 'idg', 'condtn', 'wave', 'round', 'position', 'positin1', 'order', 'partner', 'pid', 'int_corr', 'samerace', 'age_o', 'race_o', 'pf_o_att', 'pf_o_sin', 'pf_o_int', 'pf_o_fun', 'pf_o_amb', 'pf_o_sha', 'attr_o', 'sinc_o', 'intel_o', 'fun_o', 'amb_o', 'shar_o', 'like_o', 'prob_o', 'met_o', 'age', 'field_cd', 'race', 'imprace', 'imprelig', 'goal', 'date', 'go_out', 'career_c', 'sports', 'tvsports', 'exercise', 'dining', 'museums', 'art', 'hiking', 'gaming', 'clubbing', 'reading', 'tv', 'theater', 'movies', 'concerts', 'music', 'shopping', 'yoga', 'exphappy', 'attr1_1', 'sinc1_1', 'intel1_1', 'fun1_1', 'amb1_1', 'shar1_1', 'attr4_1', 'sinc4_1', 'intel4_1', 'fun4_1', 'amb4_1', 'shar4_1', 'attr2_1', 'sinc2_1', 'intel2_1', 'fun2_1', 'amb2_1', 'shar2_1', 'attr3_1', 'sinc3_1', 'fun3_1', 'intel3_1', 'amb3_1', 'attr5_1', 'sinc5_1', 'intel5_1', 'fun5_1', 'amb5_1', 'attr', 'sinc', 'intel', 'fun', 'amb', 'shar', 'like', 'prob', 'met', 'match_es', 'attr1_s', 'sinc1_s', 'in

# Modeling

# Model 1

In [41]:
# pipe line for numeric features preprocessing
np.random.seed(0)

pip_numeric = Pipeline(
    steps=[
        ('imputer', SimpleImputer()),
        ('scaler', StandardScaler())]
)

# pipe line for categorical features preprocessing

pip_categorical = Pipeline(
    steps=[
        ('imputer', SimpleImputer(strategy='constant')),
        ('onehot', OneHotEncoder(handle_unknown='ignore'))
    ]
)
# define preprocessor
preprocessor = ColumnTransformer(
    transformers=[
        ('num', pip_numeric, numeric_features),
        ('cat', pip_categorical, categorical_features)
    ]
)
#My_classifier
xgb = XGBClassifier(scale_pos_weight=1, 
                      colsample_bytree = 0.4,
                      learning_rate=0.02,
                       max_depth=11,
                      n_estimators=900,
                      subsample = 0.8,
                      objective='binary:logistic', 
                      reg_alpha = 0.3,
                    )
# combine the preprocessor with the model as a full tunable pipeline
full_pipline1 = Pipeline(
    steps=[
        ('preprocessor', preprocessor),
        ('selector', SelectKBest(mutual_info_classif, k=125)), # best 125 features
        ('my_classifier', xgb,)
    ]
)
full_pipline1

Pipeline(steps=[('preprocessor',
                 ColumnTransformer(transformers=[('num',
                                                  Pipeline(steps=[('imputer',
                                                                   SimpleImputer()),
                                                                  ('scaler',
                                                                   StandardScaler())]),
                                                  ['gender', 'idg', 'condtn',
                                                   'wave', 'round', 'position',
                                                   'positin1', 'order',
                                                   'partner', 'pid', 'int_corr',
                                                   'samerace', 'age_o',
                                                   'race_o', 'pf_o_att',
                                                   'pf_o_sin', 'pf_o_int',
                                                   'pf_o_fun', 'pf_o_amb',
                                                   'pf_o_sha', 'attr_o',
                                                   'sinc...
                               feature_types=None, gamma=None, gpu_id=None,
                               grow_policy=None, importance_type=None,
                               interaction_constraints=None, learning_rate=0.02,
                               max_bin=None, max_cat_threshold=None,
                               max_cat_to_onehot=None, max_delta_step=None,
                               max_depth=11, max_leaves=None,
                               min_child_weight=None, missing=nan,
                               monotone_constraints=None, n_estimators=900,
                               n_jobs=None, num_parallel_tree=None,
                               predictor=None, random_state=None, ...))])

In [42]:
full_pipline1 = full_pipline1.fit(X_train,y_train)    

# Hyperparameter Tuning

## Trial 1

### Model 1 , Grid Search with cross validation

In [39]:
# here we specify the search space
param_grid = {
     'preprocessor__num__imputer__strategy': ['mean'],
      'my_classifier__n_estimators': [500,700,900],     
       'my_classifier__max_depth':[8,11] ,
     
}
# cv=10 means ten-fold cross-validation

grid_search = GridSearchCV(
    full_pipline1, param_grid, cv=10, verbose=1, n_jobs=2, 
    scoring='roc_auc')

grid_search.fit(X_train, y_train)
print('best score {}'.format(grid_search.best_score_))
print('best score {}'.format(grid_search.best_params_))

Fitting 10 folds for each of 6 candidates, totalling 60 fits
best score 0.8875940721710947
best score {'my_classifier__max_depth': 8, 'my_classifier__n_estimators': 900, 'preprocessor__num__imputer__strategy': 'mean'}


I took the best 125 features and trained it with the best hyperparameters from Grid Search which is:

{'my_classifier__max_depth': 8, 'my_classifier__n_estimators': 900, 'preprocessor__num__imputer__strategy': 'mean'}

Use this model to perdict on test data and submit to kaggle

In [44]:
submission = pd.DataFrame()

submission['id'] = test_data['id']

submission['match'] = grid_search.predict_proba(test_data)[:,1]

submission.to_csv('1sample_submission_walkthrough.csv', index=False)

# After submitting to kaggle it got me a puplic score of 0.88590

I used XGBClassifier Model and used grid search for tuning hyperparameter: {'my_classifier__max_depth': 8, 'my_classifier__n_estimators': 900, 'preprocessor__num__imputer__strategy': 'mean'}

best score 0.8875940721710947

Submission on kaggle got me:

Public Score: 0.8859

Private Score: 0.8881

## Trial 2
## Random Search

In [47]:
from sklearn.model_selection import  RandomizedSearchCV#tuning by randum search
#from sklearn.model_selection import PredefinedSplit
param_grid_rs = {
      'preprocessor__num__imputer__strategy': ['mean'],
      'my_classifier__n_estimators': [700,600,900],  
      'my_classifier__max_depth':[11,13,16] ,
#       'my_classifier__learning_rate ' :[0.02,0.03,0.04]     
}

random_search = RandomizedSearchCV(
    full_pipline1, param_grid_rs, cv=10, verbose=1, n_jobs=2, 
    # number of random trials
    n_iter=5,
    scoring='roc_auc')

random_search.fit(X_train, y_train)

print('best score {}'.format(random_search.best_score_))
print('best score {}'.format(random_search.best_params_))

Fitting 10 folds for each of 5 candidates, totalling 50 fits
best score 0.8850914263641929
best score {'preprocessor__num__imputer__strategy': 'mean', 'my_classifier__n_estimators': 900, 'my_classifier__max_depth': 11}


I took the best 125 features and trained it with the best hyperparameters from Random Search which is:

{'preprocessor__num__imputer__strategy': 'mean', 'my_classifier__n_estimators': 900, 'my_classifier__max_depth': 11}

Use this model to perdict on test data and submit to kaggle

In [48]:
submission = pd.DataFrame()

submission['id'] = test_data['id']

submission['match'] = random_search.predict_proba(test_data)[:,1]

submission.to_csv('2sample_submission_walkthrough.csv', index=False)

I used XGBClassifier Model and used Random Search for tuning hyperparameter: {'preprocessor__num__imputer__strategy': 'mean', 'my_classifier__n_estimators': 900, 'my_classifier__max_depth': 11}

best score 0.8850914263641929

Submission on kaggle got me:

Public Score: 0.88493

Private Score: 0.89252

## Trial 3
## Bayesian Search

In [65]:
param_grid = {
     'preprocessor__num__imputer__strategy': ['mean'],
      'my_classifier__n_estimators': [700,900],           
      'my_classifier__max_depth':[8,11] ,}


opt = BayesSearchCV(full_pipline1, param_grid, cv=5, verbose=1, n_jobs=2, n_iter=3, scoring='roc_auc')
opt.fit(X_train,y_train)

print('best score {}'.format(opt.best_score_))

print('best score {}'.format(opt.best_params_))

Fitting 5 folds for each of 1 candidates, totalling 5 fits
Fitting 5 folds for each of 1 candidates, totalling 5 fits
Fitting 5 folds for each of 1 candidates, totalling 5 fits
best score 0.8833531568248999
best score OrderedDict([('my_classifier__max_depth', 11), ('my_classifier__n_estimators', 883), ('preprocessor__num__imputer__strategy', 'mean')])


I took the best 125 features and trained it with the best hyperparameters from Bayesian Search which is:

('my_classifier__max_depth', 11), ('my_classifier__n_estimators', 883), ('preprocessor__num__imputer__strategy', 'mean')

Use this model to perdict on test data and submit to kaggle

In [66]:
submission = pd.DataFrame()

submission['id'] = test_data['id']

submission['match'] = opt.predict_proba(test_data)[:,1]

submission.to_csv('3sample_submission_walkthrough.csv', index=False)

I used XGBClassifier Model and used Random Search for tuning hyperparameter: 'my_classifier__max_depth', 11), ('my_classifier__n_estimators', 883), ('preprocessor__num__imputer__strategy', 'mean')

best score 0.8833531568248999

Submission on kaggle got me:

Public Score: 0.8845

Private Score: 0.89126

## Trial 4 

## Model 2

changed the model to GradientBoostingClassifier and use Grid Search with it

In [74]:
# pipe line for numeric features preprocessing
np.random.seed(0)

pip_numeric = Pipeline(
    steps=[
        ('imputer', SimpleImputer()),
        ('scaler', StandardScaler())]
)

# pipe line for categorical features preprocessing

pip_categorical = Pipeline(
    steps=[
        ('imputer', SimpleImputer(strategy='constant')),
        ('onehot', OneHotEncoder(handle_unknown='ignore'))
    ]
)
# define preprocessor
preprocessor = ColumnTransformer(
    transformers=[
        ('num', pip_numeric, numeric_features),
        ('cat', pip_categorical, categorical_features)
    ]
)
#My_classifier
model = GradientBoostingClassifier( min_samples_split=500,max_features='sqrt',
                                   subsample=0.8,random_state=42,max_depth=11,n_estimators=900,learning_rate=0.02)

# combine the preprocessor with the model as a full tunable pipeline
full_pipline2 = Pipeline(
    steps=[
        ('preprocessor', preprocessor),
        ('selector', SelectKBest(mutual_info_classif, k=125)), # best 125 features
        ('my_classifier', xgb,)
    ]
)
full_pipline2

Pipeline(steps=[('preprocessor',
                 ColumnTransformer(transformers=[('num',
                                                  Pipeline(steps=[('imputer',
                                                                   SimpleImputer()),
                                                                  ('scaler',
                                                                   StandardScaler())]),
                                                  ['gender', 'idg', 'condtn',
                                                   'wave', 'round', 'position',
                                                   'positin1', 'order',
                                                   'partner', 'pid', 'int_corr',
                                                   'samerace', 'age_o',
                                                   'race_o', 'pf_o_att',
                                                   'pf_o_sin', 'pf_o_int',
                                                   'pf_o_fun', 'pf_o_amb',
                                                   'pf_o_sha', 'attr_o',
                                                   'sinc...
                               feature_types=None, gamma=None, gpu_id=None,
                               grow_policy=None, importance_type=None,
                               interaction_constraints=None, learning_rate=0.02,
                               max_bin=None, max_cat_threshold=None,
                               max_cat_to_onehot=None, max_delta_step=None,
                               max_depth=11, max_leaves=None,
                               min_child_weight=None, missing=nan,
                               monotone_constraints=None, n_estimators=900,
                               n_jobs=None, num_parallel_tree=None,
                               predictor=None, random_state=None, ...))])

In [75]:
param_grid = {
      'preprocessor__num__imputer__strategy': ['mean' , 'constant'], 
      'my_classifier__max_depth':[6,8,10] ,
#       'my_classifier__learning_rate ' :[0.02,0.04,0.06]   
}

grid_search = GridSearchCV(
    full_pipline2, param_grid, cv=10, verbose=1, n_jobs=2, 
    scoring='roc_auc')

grid_search.fit(X_train, y_train)
print('best score {}'.format(grid_search.best_score_))
print('best score {}'.format(grid_search.best_params_))

Fitting 10 folds for each of 3 candidates, totalling 30 fits
best score 0.8872820121413671
best score {'my_classifier__max_depth': 8, 'preprocessor__num__imputer__strategy': 'mean'}


I took the best 125 features and trained it with the best hyperparameters from Grid Search which is:

'my_classifier__max_depth': 8, 'preprocessor__num__imputer__strategy': 'mean'

Use this model to perdict on test data and submit to kaggle

In [76]:
submission = pd.DataFrame()

submission['id'] = test_data['id']

submission['match'] = grid_search.predict_proba(test_data)[:,1]

submission.to_csv('4sample_submission_walkthrough.csv', index=False)

I used GradientBoostingClassifier Model and used Grid Search  for tuning hyperparameter: 'my_classifier__max_depth': 8, 'preprocessor__num__imputer__strategy': 'mean'

best score 0.8872820121413671

Submission on kaggle got me:

Public Score: 0.88537

Private Score: 0.89114

## Trial 5
## Model 2 with bayesian search

In [77]:
opt = BayesSearchCV(full_pipline2, param_grid, cv=5, verbose=1, n_jobs=2, n_iter=3, scoring='roc_auc')
opt.fit(X_train,y_train)

print('best score {}'.format(opt.best_score_))

print('best score {}'.format(opt.best_params_))

Fitting 5 folds for each of 1 candidates, totalling 5 fits
Fitting 5 folds for each of 1 candidates, totalling 5 fits
Fitting 5 folds for each of 1 candidates, totalling 5 fits
best score 0.8853224706931636
best score OrderedDict([('my_classifier__max_depth', 6), ('preprocessor__num__imputer__strategy', 'mean')])


I took the best 125 features and trained it with the best hyperparameters from bayesian Search which is:

('my_classifier__max_depth', 6), ('preprocessor__num__imputer__strategy', 'mean')

Use this model to perdict on test data and submit to kaggle

In [78]:
submission = pd.DataFrame()

submission['id'] = test_data['id']

submission['match'] = opt.predict_proba(test_data)[:,1]

submission.to_csv('5sample_submission_walkthrough.csv', index=False)

I used GradientBoostingClassifier Model and used bayesian search  for tuning hyperparameter: 'my_classifier__max_depth': 8, 'preprocessor__num__imputer__strategy': 'mean'

best score 0.8853224706931636

Submission on kaggle got me:

Public Score: 0.8827

Private Score: 0.87177

## Trial 6

# Model 3 

Use Decision Tree classifier with the whole data set and do Grid Search on it

In [81]:
np.random.seed(0)
# define a pipe line for numeric feature preprocessing
# we gave them a name so we can set their hyperparameters
transformer_numeric = Pipeline(
    steps=[
        ('imputer', SimpleImputer()),
        ('scaler', StandardScaler())]
)

# define a pipe line for categorical feature preprocessing
# we gave them a name so we can set their hyperparameters
transformer_categorical = Pipeline(
    steps=[
        ('imputer', SimpleImputer(strategy='constant')),
        ('onehot', OneHotEncoder(handle_unknown='ignore'))
    ]
)
# define the preprocessor 
# we gave them a name so we can set their hyperparameters
# we also specify what are the categorical 
preprocessor = ColumnTransformer(
    transformers=[
        ('num', transformer_numeric, numeric_features),
        ('cat', transformer_categorical, categorical_features)
    ]
)

# combine the preprocessor with the model as a full tunable pipeline
# we gave them a name so we can set their hyperparameters
full_pipline3 = Pipeline(
    steps=[
        ('preprocessor', preprocessor),
        ('my_classifier', DecisionTreeClassifier(),)
    ]
)
full_pipline3

Pipeline(steps=[('preprocessor',
                 ColumnTransformer(transformers=[('num',
                                                  Pipeline(steps=[('imputer',
                                                                   SimpleImputer()),
                                                                  ('scaler',
                                                                   StandardScaler())]),
                                                  ['gender', 'idg', 'condtn',
                                                   'wave', 'round', 'position',
                                                   'positin1', 'order',
                                                   'partner', 'pid', 'int_corr',
                                                   'samerace', 'age_o',
                                                   'race_o', 'pf_o_att',
                                                   'pf_o_sin', 'pf_o_int',
                                                   'pf_o_fun', 'pf_o_amb',
                                                   'pf_o_sha', 'attr_o',
                                                   'sinc_o', 'intel_o', 'fun_o',
                                                   'amb_o', 'shar_o', 'like_o',
                                                   'prob_o', 'met_o', 'age', ...]),
                                                 ('cat',
                                                  Pipeline(steps=[('imputer',
                                                                   SimpleImputer(strategy='constant')),
                                                                  ('onehot',
                                                                   OneHotEncoder(handle_unknown='ignore'))]),
                                                  ['field', 'undergra', 'from',
                                                   'zipcode', 'income',
                                                   'career'])])),
                ('my_classifier', DecisionTreeClassifier())])

In [91]:
# here we specify the search space
# n_components = list(range(1,X_train.shape[1]+1,1))
param_grid = {
     'preprocessor__num__imputer__strategy': ['mean'],
      'my_classifier__max_depth':[5,8,11] ,
    'my_classifier__criterion':['gini', 'entropy'],
    'my_classifier__min_samples_leaf':[1,2,3]
}
     
# cv=10 means ten-fold cross-validation

grid_search = GridSearchCV(
    full_pipline3, param_grid, cv=10, verbose=1, n_jobs=2, 
    scoring='roc_auc')

grid_search.fit(X_train, y_train)
print('best score {}'.format(grid_search.best_score_))
print('best score {}'.format(grid_search.best_params_))

Fitting 10 folds for each of 18 candidates, totalling 180 fits
best score 0.8200167385896512
best score {'my_classifier__criterion': 'entropy', 'my_classifier__max_depth': 5, 'my_classifier__min_samples_leaf': 1, 'preprocessor__num__imputer__strategy': 'mean'}


I took the features and trained it with the best hyperparameters from Grid Search which is:

'my_classifier__criterion': 'entropy', 'my_classifier__max_depth': 5, 'my_classifier__min_samples_leaf': 1, 'preprocessor__num__imputer__strategy': 'mean'

Use this model to perdict on test data and submit to kaggle

In [93]:
submission = pd.DataFrame()

submission['id'] = test_data['id']

submission['match'] = grid_search.predict_proba(test_data)[:,1]

submission.to_csv('6sample_submission_walkthrough.csv', index=False)

# Got me puplic score of 0.81142

I used Decision Tree classifier with the whole data set and do Grid Search for tuning hyperparameter: 'my_classifier__criterion': 'entropy', 'my_classifier__max_depth': 5, 'my_classifier__min_samples_leaf': 1, 'preprocessor__num__imputer__strategy': 'mean'

best score 0.8200167385896512

Submission on kaggle got me:

Public Score: 0.81142

Private Score: 0.82896

# Conclusion

Best submission is for trial 2 which got me a puplic score of 0.88493 on Kaggle and 0.89252 For private score.

My private score which is 0.89252 got me the second place in the leader board on kaggle.